In [ ]:
from client import Client
import time
from urllib.request import urlopen

In [ ]:
import os

In [ ]:
client = Client()
client.login('PUT YOUR API KEY HERE')

In [ ]:
result = client.upload('image1.fits')

In [ ]:
result

In [ ]:
assert(result['status'] == 'success')
subid = result['subid']
while True:
    stat = client.sub_status(subid, justdict=True)
    print('Got status:', stat)
    jobs = stat.get('jobs', [])
    if len(jobs):
        for j in jobs:
            if j is not None:
                break
        if j is not None:
            print('Selecting job id', j)
            jobid = j
            break
    time.sleep(5)


In [ ]:
while True:
    stat = client.job_status(jobid, justdict=True)
    print('Got job status:', stat)
    if stat.get('status','') in ['success']:
        success = (stat['status'] == 'success')
        break
    elif stat.get('status','') in ['failure']:
        print("Image solving failed")
        break
    time.sleep(5)

In [ ]:
retrieveurls = []
url = client.apiurl.replace('/api/', '/new_fits_file/%i/' % jobid)
retrieveurls.append((url, 'new-1.fits'))
for url,fn in retrieveurls:
    print('Retrieving file from', url, 'to', fn)
    f = urlopen(url)
    txt = f.read()
    w = open(fn, 'wb')
    w.write(txt)
    w.close()
    print('Wrote to', fn)